<a href="https://colab.research.google.com/github/mohithxoxo/News-Scapper-and-Fake-News-Detection/blob/master/news_scraper.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Download articles 

In [ ]:
!pip install newspaper3k

     |████████████████████████████████| 215kB 4.5MB/s 
     |████████████████████████████████| 7.4MB 6.3MB/s 
     |████████████████████████████████| 51kB 4.5MB/s 
  Created wheel for jieba3k: filename=jieba3k-0.35.1-cp36-none-any.whl size=7398406 sha256=b5fe257b128ed8ee37b72c9a3f326a84f1a5deccf6cc25bdc7fb44baf980862e
  Stored in directory: /root/.cache/pip/wheels/83/15/9c/a3f1f67e7f7181170ad37d32e503c35da20627c013f438ed34
  Created wheel for feedfinder2: filename=feedfinder2-0.0.4-cp36-none-any.whl size=3355 sha256=e1bb83a19ea9576b2556097ecb4d2622197989bba21cee4f1b70c54f226ff052
  Stored in directory: /root/.cache/pip/wheels/de/03/ca/778e3a7a627e3d98836cc890e7cb40c7575424cfd3340f40ed
  Created wheel for tinysegmenter: filename=tinysegmenter-0.3-cp36-none-any.whl size=13538 sha256=74e8482ef0366a2ea1bedbfd663dcf18d29c17e2d616737754ef8bc99e3a18eb
  Stored in directory: /root/.cache/pip/wheels/81/2b/43/a02ede72324dd40cdd7ca53aad718c7710628e91b8b0dc0f02
Successfully built jieba3k feedfinde

In [ ]:
import feedparser as fp
import json 
import newspaper
from newspaper import Article 
from time import mktime
from datetime import datetime


In [ ]:
#set the limit from number of articles to download 
LIMIT=10000

data={}
data['newspapers']={}

In [ ]:
#links of different sites to download articles from them 
dic={
  "cnn": {
    "link": "http://edition.cnn.com/"
  },
  "bbc": {
    "rss": "http://feeds.bbci.co.uk/news/rss.xml",
    "link": "http://www.bbc.com/"
  },
  "breitbart": {
    "link": "http://www.breitbart.com/"
  },
  "infowars": {
    "link": "https://www.infowars.com/"
  },
  "washingtonpost": {
    "rss": "http://feeds.washingtonpost.com/rss/world",
    "link": "https://www.washingtonpost.com/"
  } 
}

In [ ]:
dic

{'bbc': {'link': 'http://www.bbc.com/',
  'rss': 'http://feeds.bbci.co.uk/news/rss.xml'},
 'breitbart': {'link': 'http://www.breitbart.com/'},
 'cnn': {'link': 'http://edition.cnn.com/'},
 'infowars': {'link': 'https://www.infowars.com/'},
 'washingtonpost': {'link': 'https://www.washingtonpost.com/',
  'rss': 'http://feeds.washingtonpost.com/rss/world'}}

In [ ]:
json_object=json.dumps(dic,indent=4)

In [ ]:
with open("NewsPapers.json", "w") as outfile: 
    outfile.write(json_object)

In [ ]:
# Loads the JSON files with news sites
with open('NewsPapers.json') as data_file:
    companies = json.load(data_file)

In [ ]:
companies

{'bbc': {'link': 'http://www.bbc.com/',
  'rss': 'http://feeds.bbci.co.uk/news/rss.xml'},
 'breitbart': {'link': 'http://www.breitbart.com/'},
 'cnn': {'link': 'http://edition.cnn.com/'},
 'infowars': {'link': 'https://www.infowars.com/'},
 'washingtonpost': {'link': 'https://www.washingtonpost.com/',
  'rss': 'http://feeds.washingtonpost.com/rss/world'}}

In [ ]:
count=1
#iterate through each news company 
for company, value in companies.items():
    # If a RSS link is provided in the JSON file, this will be the first choice.
    # Reason for this is that, RSS feeds often give more consistent and correct data.
    # If you do not want to scrape from the RSS-feed, just leave the RSS attr empty in the JSON file.
    if 'rss' in value:
        d = fp.parse(value['rss'])
        print("Downloading articles from ", company)
        newsPaper = {
            "rss": value['rss'],
            "link": value['link'],
            "articles": []
        }
        for entry in d.entries:
            # Check if publish date is provided, if no the article is skipped.
            # This is done to keep consistency in the data and to keep the script from crashing.
            # we will use hasattr() to know if entry has published attribute
            if hasattr(entry, 'published'):
                if count > LIMIT:
                    break
                article = {}
                article['link'] = entry.link
                date = entry.published_parsed
                article['published'] = datetime.fromtimestamp(mktime(date)).isoformat()
                try:
                    content = Article(entry.link,language="en")
                    content.download()
                    content.parse()
                except Exception as e:
                    # If the download for some reason fails (ex. 404) the script will continue downloading
                    # the next article.
                    print(e)
                    print("continuing...")
                    continue
                article['title'] = content.title
                article['text'] = content.text
                newsPaper['articles'].append(article)
                print(count, "articles downloaded from", company, ", url: ", entry.link)
                count = count + 1
    else:
        # This is the fallback method if a RSS-feed link is not provided.
        # It uses the python newspaper library to extract articles
        print("Building site for ", company)
        paper = newspaper.build(value['link'], memoize_articles=False,language="en")
        newsPaper = {
            "link": value['link'],
            "articles": []
        }
        noneTypeCount = 0
        for content in paper.articles:
            if count > LIMIT:
                break
            try:
                content.download()
                content.parse()
            except Exception as e:
                print(e)
                print("continuing...")
                continue
            # Again, for consistency, if there is no found publish date the article will be skipped.
            # After 100 downloaded articles from the same newspaper without publish date, the company will be skipped.
            if content.publish_date is None:
                #print(count, " Article has date of type None...")
                noneTypeCount = noneTypeCount + 1
                if noneTypeCount > 100:
                    print("Too many noneType dates, aborting...")
                    noneTypeCount = 0
                    break
                count = count + 1
                continue
            article = {}
            article['title'] = content.title
            article['text'] = content.text
            article['link'] = content.url
            article['published'] = content.publish_date.isoformat()
            newsPaper['articles'].append(article)
            print(count, "articles downloaded from", company, " using newspaper, url: ", content.url)
            count = count + 1
            noneTypeCount = 0
    count = 1
    data['newspapers'][company] = newsPaper

# Finally it saves the articles as a JSON-file.
try:
    with open('scraped_articles.json', 'w') as outfile:
        json.dump(data, outfile)
except Exception as e:
    print(e)

Building site for  cnn
3 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/10/africa/mukwege-nobel-prize-death-threats/index.html
4 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/10/africa/george-bizos-death/index.html
5 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/11/africa/tresemme-clicks-ad-south-africa/index.html
6 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/09/sport/caster-semenya-ruling-athletics-spt-intl/index.html
7 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/08/africa/clicks-hair-ad-south-africa/index.html
8 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/07/africa/africa-engineering-prize-intl/index.html
9 articles downloaded from cnn  using newspaper, url:  http://edition.cnn.com/2020/09/02/africa/paul-rusesabagina-rwanda-arrest-intl/index.html
10 artic

In [ ]:
with open('scraped_articles.json') as json_data:
    d = json.load(json_data)

In [ ]:
for i, site in enumerate((list(d['newspapers']))):
    print(i, site)

0 cnn
1 bbc
2 breitbart
3 infowars
4 washingtonpost


In [ ]:
d

{'newspapers': {'bbc': {'articles': [{'link': 'https://www.bbc.co.uk/news/uk-54163683',
     'published': '2020-09-15T13:02:03',
     'text': 'Image copyright HoC\n\nIt will take a "matter of weeks" to resolve the problems around coronavirus testing, Health Secretary Matt Hancock has said.\n\nHe told MPs there had been a "sharp rise" in those seeking a test, "including those who are not eligible".\n\nThe tests should be prioritised for those who need it most, including those in care homes, he said.\n\nBut shadow health secretary Jonathan Ashworth said no tests were available in virus "hotspots" over the weekend.\n\nIt comes after widespread reports of people struggling to get tested, with hospital bosses warning that a lack of tests for NHS workers was putting services at risk.\n\nAn increase in demand for coronavirus tests has led to local shortages, with some people being directed to test sites hundreds of miles from their homes.\n\nAround 220,000 tests are processed each day, accord

In [ ]:
import pandas as pd
for i, site in enumerate((list(d['newspapers']))):
    articles = list(d['newspapers'][site]['articles'])
    if i == 0:
        df = pd.DataFrame.from_dict(articles)
        df["site"] = site
    else:
        new_df = pd.DataFrame.from_dict(articles)
        new_df["site"] = site
        df = pd.concat([df, new_df], ignore_index = True)

In [ ]:
df.shape

(1496, 5)

In [ ]:
df

title  ...            site
0     Nobel Peace Prize winner Denis Mukwege under U...  ...             cnn
1     George Bizos, renowned human rights lawyer who...  ...             cnn
2     South Africa retailers remove TRESemmé product...  ...             cnn
3     Caster Semenya loses appeal in Swiss court ove...  ...             cnn
4     Protests erupt in South Africa over controvers...  ...             cnn
...                                                 ...  ...             ...
1491  UN experts decry continued abuse as Syria’s wa...  ...  washingtonpost
1492  Diplomats: Roadside bombing targets British co...  ...  washingtonpost
1493  Vietnam sentences 7 for human smuggling to Bri...  ...  washingtonpost
1494  India accuses China of violating pacts, milita...  ...  washingtonpost
1495  Shortage of virus tests in UK hurts effort to ...  ...  washingtonpost

[1496 rows x 5 columns]

In [ ]:
#convert it to csv file 
df.to_csv(r'news.csv', index = False, header=True)